In [1]:
from google.colab import drive
drive.mount('/content/gdrive' , force_remount=True)

Mounted at /content/gdrive


In [7]:
%cd /content/gdrive/MyDrive

/content/gdrive/MyDrive


# wav2lip setup

In [ ]:
!git clone https://github.com/justinjohn0306/Wav2Lip

fatal: destination path 'Wav2Lip' already exists and is not an empty directory.


In [10]:
!cd Wav2Lip && pip install -r requirements.txt

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [11]:
!pip install ffmpeg-python

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip uninstall tensorflow tensorflow-gpu

In [ ]:
#download the pretrained model
!wget 'https://iiitaphyd-my.sharepoint.com/personal/radrabha_m_research_iiit_ac_in/_layouts/15/download.aspx?share=EdjI7bZlgApMqsVoEUUXpLsBxqXbn5z8VTmoxp55YNDcIA' -O 'Wav2Lip/checkpoints/wav2lip_gan.pth'
a = !pip install https://raw.githubusercontent.com/AwaleSajil/ghc/master/ghc-1.0-py3-none-any.whl

#download pretrained model for face detection
!wget "https://www.adrianbulat.com/downloads/python-fan/s3fd-619a316812.pth" -O "Wav2Lip/face_detection/detection/sfd/s3fd.pth"

# Youtube video setup

In [12]:
!pip install yt-dlp

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import os

#@markdown ## Find YouTube video ID from URL

#@markdown ___

#@markdown Link format:

#@markdown ``https://youtu.be/vAnWYLTdvfY`` ❌

#@markdown ``https://www.youtube.com/watch?v=vAnWYLTdvfY`` ✔️

!rm -df youtube.mp4

#@markdown ___
from urllib import parse as urlparse
YOUTUBE_URL = 'https://www.youtube.com/watch?v=YMuuEv37s0o' #@param {type:"string"}
url_data = urlparse.urlparse(YOUTUBE_URL)
query = urlparse.parse_qs(url_data.query)
YOUTUBE_ID = query["v"][0]

# remove previous input video
!rm -f input_vid.mp4


#@markdown ___

#@markdown ### Trim the video (start, end) seconds
start = 0 #@param {type:"integer"}
end = 67 #@param {type:"integer"}
interval = end - start

#@markdown <font color="orange"> Note: ``the trimmed video must have face on all frames``

# Download the YouTube video using yt-dlp
!yt-dlp -f 'bestvideo[ext=mp4]' --output "youtube.%(ext)s" https://www.youtube.com/watch?v=$YOUTUBE_ID

# Cut the video using FFmpeg
!ffmpeg -y -i youtube.mp4 -ss {start} -t {interval} -async 1 input_vid.mp4

[youtube] Extracting URL: https://www.youtube.com/watch?v=YMuuEv37s0o
[youtube] YMuuEv37s0o: Downloading webpage
[youtube] YMuuEv37s0o: Downloading ios player API JSON
[youtube] YMuuEv37s0o: Downloading android player API JSON
[youtube] YMuuEv37s0o: Downloading m3u8 information
[info] YMuuEv37s0o: Downloading 1 format(s): 628
[hlsnative] Downloading m3u8 manifest
[hlsnative] Total fragments: 117
[download] Destination: youtube.mp4
[download] 100% of    1.16GiB in 00:01:02 at 18.89MiB/s
ffmpeg version 4.2.7-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 9 (Ubuntu 9.4.0-1ubuntu1~20.04.1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-avresample --disable-filter=resample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca 

In [ ]:
# Preview the trimmed video
from IPython.display import HTML
from base64 import b64encode
mp4 = open('input_vid.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""<video width=600 controls><source src="{data_url}"></video>""")

In [ ]:
import os
from IPython.display import Audio
from IPython.core.display import display
from IPython.display import clear_output
import librosa
import soundfile as sf

# Define the path to your audio
#@markdown ``Add the full path to your audio on your Gdrive`` 👇
PATH_TO_YOUR_AUDIO = 'output10.wav' #@param {type:"string"}

# Remove previous input audio if exists
if os.path.isfile('input_audio.wav'):
    os.remove('input_audio.wav')

# Load audio with specified sampling rate
audio, sr = librosa.load(PATH_TO_YOUR_AUDIO, sr=None)

# Save audio with specified sampling rate
sf.write('input_audio.wav', audio, sr, format='wav')

# Function to display audio
def displayAudio():
  display(Audio('input_audio.wav'))

# Display the audio
clear_output()
displayAudio()


In [17]:
from IPython.display import HTML
from base64 import b64encode
from IPython.display import clear_output

def showVideo(path):
  mp4 = open(str(path),'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
  return HTML("""
  <video width=700 controls>
        <source src="%s" type="video/mp4">
  </video>
  """ % data_url)

In [ ]:
#@markdown <b>Note: Only change these, if you have to</b>
pad_top =  0#@param {type:"integer"}
pad_bottom =  10#@param {type:"integer"}
pad_left =  0#@param {type:"integer"}
pad_right =  0#@param {type:"integer"}
rescaleFactor =  1#@param {type:"integer"}
nosmooth = False #@param {type:"boolean"}


if nosmooth == False:
  !cd Wav2Lip && python inference.py --checkpoint_path checkpoints/wav2lip_gan.pth --face "/content/gdrive/MyDrive/input_vid.mp4" --audio "/content/gdrive/MyDrive/input_audio.wav" --pads $pad_top $pad_bottom $pad_left $pad_right --resize_factor $rescaleFactor
else:
  !cd Wav2Lip && python inference.py --checkpoint_path checkpoints/wav2lip_gan.pth --face "/content/gdrive/MyDrive/input_vid.mp4" --audio "/content/gdrive/MyDrive/input_audio.wav" --pads $pad_top $pad_bottom $pad_left $pad_right --resize_factor $rescaleFactor --nosmooth

clear_output()
print("Final Video Preview")
print("Download this video from", 'Wav2Lip/results/result_voice.mp4')


Using cuda for inference.
Reading video frames...
